# `blastx` to GOslim

In this notebook, I'll take my `blastx` output for mRNA transcripts and match each transcript with GOslim. This way, I can group DMG and genes with DML more easily. My script was modified from [this Jupyter notebook](https://github.com/sr320/nb-2018/blob/master/C_virginica/83-blast-2-slim.ipynb).

## 0. Set working directory

In [1]:
pwd

'/Users/yaamini/Documents/yaamini-virginica/notebooks'

In [2]:
cd ../analyses/2019-08-14-Differentially-Methylated-Genes/

/Users/yaamini/Documents/yaamini-virginica/analyses/2019-08-14-Differentially-Methylated-Genes


## 1. Download files and set variable paths

The directory needs the following files:

- Uniprot GO annotation file (340M) available here http://owl.fish.washington.edu/halfshell/bu-alanine-wd/17-07-20/uniprot-SP-GO.sorted
- GOslim file available here http://owl.fish.washington.edu/halfshell/bu-alanine-wd/17-07-20/GO-GOslim.sorted
- `blastx` output file in format -6

In [3]:
!curl -O http://owl.fish.washington.edu/halfshell/bu-alanine-wd/17-07-20/uniprot-SP-GO.sorted

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  340M  100  340M    0     0  13.6M      0  0:00:24  0:00:24 --:--:-- 19.7M


In [4]:
!curl -O http://owl.fish.washington.edu/halfshell/bu-alanine-wd/17-07-20/GO-GOslim.sorted

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 2314k  100 2314k    0     0  5771k      0 --:--:-- --:--:-- --:--:-- 5964k


In [28]:
!head ../2018-12-02-Gene-Enrichment-Analysis/2018-09-11-Transcript-Uniprot-blastx-codeIsolated.txt

## 2. Match `blastx` to GOslim terms

No code below needs to be modified!

In [29]:
#reducing number of columns and sorting to get spid evlaue - 
!awk -v OFS='\t' '{print $3, $1, $13}' < ../2018-12-02-Gene-Enrichment-Analysis/2018-09-11-Transcript-Uniprot-blastx-codeIsolated.txt | sort \
> _blast-sort.tab

In [30]:
!head -2 _blast-sort.tab

A0A084API3	XM_022442998.1	5.9
A0A086F3E3	XM_022443134.1	0.23


In [31]:
#joining blast with uniprot annoation file and reducing to three columns UniprotID, Query, All GO terms
!join -t $'\t' \
_blast-sort.tab \
uniprot-SP-GO.sorted \
| cut -f1,2,14 \
> _blast-annot.tab

In [32]:
!head -2 _blast-annot.tab

A0A086F3E3	XM_022443134.1	GO:0016021; GO:0022841; GO:0071805
A0A0A6YXX9	XM_022439761.1	


In [33]:
%%bash 

# This script was originally written to address a specific problem that Rhonda was having



# input_file is the initial, "problem" file
# file is an intermediate file that most of the program works upon
# output_file is the final file produced by the script
input_file="_blast-annot.tab"
file="_intermediate.file"
output_file="_blast-GO-unfolded.tab"

# sed command substitutes the "; " sequence to a tab and writes the new format to a new file.
# This character sequence is how the GO terms are delimited in their field.
sed $'s/; /\t/g' "$input_file" > "$file"

# Identify first field containing a GO term.
# Search file with grep for "GO:" and pipe to awk.
# Awk sets tab as field delimiter (-F'\t'), runs a for loop that looks for "GO:" (~/GO:/), and then prints the field number).
# Awk results are piped to sort, which sorts unique by number (-ug).
# Sort results are piped to head to retrieve the lowest value (i.e. the top of the list; "-n1").
begin_goterms=$(grep "GO:" "$file" | awk -F'\t' '{for (i=1;i<=NF;i++) if($i ~/GO:/) print i}' | sort -ug | head -n1)

# While loop to process each line of the input file.
while read -r line
	do
	
	# Send contents of the current line to awk.
	# Set the field separator as a tab (-F'\t') and print the number of fields in that line.
	# Save the results of the echo/awk pipe (i.e. number of fields) to the variable "max_field".
	max_field=$(echo "$line" | awk -F'\t' '{print NF}')

	# Send contents of current line to cut.
	# Cut fields (i.e. retain those fields) 1-12.
	# Save the results of the echo/cut pipe (i.e. fields 1-12) to the variable "fixed_fields"
	fixed_fields=$(echo "$line" | cut -f1-2)

	# Since not all the lines contain the same number of fields (e.g. may not have GO terms),
	# evaluate the number of fields in each line to determine how to handle current line.

	# If the value in max_field is less than the field number where the GO terms begin,
	# then just print the current line (%s) followed by a newline (\n).
	if (( "$max_field" < "$begin_goterms" ))
		then printf "%s\n" "$line"
			else

			# Send contents of current line (which contains GO terms) to cut.
			# Cut fields (i.e. retain those fields) 13 to whatever the last field is in the curent line.
			# Save the results of the echo/cut pipe (i.e. all the GO terms fields) to the variable "goterms".
			goterms=$(echo "$line" | cut -f"$begin_goterms"-"$max_field")
			
			# Assign values in the variable "goterms" to a new indexed array (called "array"), 
			# with tab delimiter (IFS=$'\t')
			IFS=$'\t' read -r -a array <<<"$goterms"
			
			# Iterate through each element of the array.
			# Print the first 12 fields (i.e. the fields stored in "fixed_fields") followed by a tab (%s\t).
			# Print the current element in the array (i.e. the current GO term) followed by a new line (%s\n).
			for element in "${!array[@]}"	
				do printf "%s\t%s\n" "$fixed_fields" "${array[$element]}"
			done
	fi

# Send the input file into the while loop and send the output to a file named "rhonda_fixed.txt".
done < "$file" > "$output_file"

In [34]:
!head _blast-GO-unfolded.tab

A0A086F3E3	XM_022443134.1	GO:0016021
A0A086F3E3	XM_022443134.1	GO:0022841
A0A086F3E3	XM_022443134.1	GO:0071805
A0A0A6YXX9	XM_022439761.1
A0A0A7DNP6	XM_022463864.1	GO:0005576
A0A0A7DNP6	XM_022463864.1	GO:0007218
A0A0B4J1F4	XM_022466820.1	GO:0005768
A0A0B4J1F4	XM_022466820.1	GO:0005769
A0A0B4J1F4	XM_022466820.1	GO:0005886
A0A0B4J1F4	XM_022466820.1	GO:0051443


In [42]:
!awk '{print $3"\t"$2}' _blast-GO-unfolded.tab | sort -V > _blast-GO-unfolded.sorted

In [43]:
#extra space was removed tw
!head _blast-GO-unfolded.sorted

GO:0000001	XM_022439334.1
GO:0000001	XM_022439801.1
GO:0000001	XM_022449404.1
GO:0000001	XM_022454917.1
GO:0000001	XM_022454918.1
GO:0000001	XM_022454919.1
GO:0000001	XM_022454920.1
GO:0000001	XM_022457838.1
GO:0000001	XM_022457839.1
GO:0000001	XM_022458199.1


In [39]:
!head GO-GOslim.sorted

GO:0000001	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000002	mitochondrial genome maintenance	cell organization and biogenesis	P
GO:0000003	reproduction	other biological processes	P
GO:0000006	high affinity zinc uptake transmembrane transporter activity	transporter activity	F
GO:0000007	low-affinity zinc ion transmembrane transporter activity	transporter activity	F
GO:0000009	"alpha-1,6-mannosyltransferase activity"	other molecular function	F
GO:0000010	trans-hexaprenyltranstransferase activity	other molecular function	F
GO:0000011	vacuole inheritance	cell organization and biogenesis	P
GO:0000012	single strand break repair	DNA metabolism	P
GO:0000012	single strand break repair	stress response	P


In [44]:
!join -1 1 -2 1 -t $'\t' \
_blast-GO-unfolded.sorted \
GO-GOslim.sorted | head

GO:0000001	XM_022439334.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022439801.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022449404.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022454917.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022454918.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022454919.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022454920.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022457838.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022457839.1	mitochondrion inheritance	cell organization and biogenesis	P
GO:0000001	XM_022458199.1	mitochondrion inheritance	cell organization and biogenesis	P
join: stdout: Broken pipe


In [45]:
#joining files to get GOslim for each query (with duplicate GOslim / query removed)
!join -1 1 -2 1 -t $'\t' \
_blast-GO-unfolded.sorted \
GO-GOslim.sorted \
| uniq | awk -F'\t' -v OFS='\t' '{print $2, $4, $5}' \
> Blastquery-GOslim.tab
!wc -l Blastquery-GOslim.tab

  943822 Blastquery-GOslim.tab


In [46]:
!head Blastquery-GOslim.tab
!wc -l Blastquery-GOslim.tab

XM_022439334.1	cell organization and biogenesis	P
XM_022439801.1	cell organization and biogenesis	P
XM_022449404.1	cell organization and biogenesis	P
XM_022454917.1	cell organization and biogenesis	P
XM_022454918.1	cell organization and biogenesis	P
XM_022454919.1	cell organization and biogenesis	P
XM_022454920.1	cell organization and biogenesis	P
XM_022457838.1	cell organization and biogenesis	P
XM_022457839.1	cell organization and biogenesis	P
XM_022458199.1	cell organization and biogenesis	P
  943822 Blastquery-GOslim.tab


## 3. Get Biological Process GOslim terms

In [9]:
!awk -F"\t" '$3 == "P" { print $1"\t"$2 }' Blastquery-GOslim.tab | sort > Blastquery-GOslim-BP.sorted
!head Blastquery-GOslim-BP.sorted

XM_022430339.1	cell cycle and proliferation
XM_022430339.1	developmental processes
XM_022430339.1	other biological processes
XM_022430339.1	other biological processes
XM_022430339.1	other metabolic processes
XM_022430339.1	other metabolic processes
XM_022430339.1	other metabolic processes
XM_022430339.1	other metabolic processes
XM_022430339.1	other metabolic processes
XM_022430339.1	other metabolic processes


In [3]:
#Remove duplicate entries
#Count the number of unique entries
!uniq Blastquery-GOslim-BP.sorted > Blastquery-GOslim-BP.sorted.unique
!head Blastquery-GOslim-BP.sorted.unique
!wc -l Blastquery-GOslim-BP.sorted.unique

XM_022430339.1	cell cycle and proliferation
XM_022430339.1	developmental processes
XM_022430339.1	other biological processes
XM_022430339.1	other metabolic processes
XM_022430339.1	transport
XM_022430340.1	cell cycle and proliferation
XM_022430340.1	cell organization and biogenesis
XM_022430341.1	cell cycle and proliferation
XM_022430341.1	cell organization and biogenesis
XM_022430342.1	cell cycle and proliferation
  133787 Blastquery-GOslim-BP.sorted.unique


In [4]:
#Count the number of unique IDs with GOSlim terms
!uniq -f1 Blastquery-GOslim-BP.sorted.unique | wc -l

  126112


In [5]:
#Remove all "other biological processes"
#Confirm removal
#Count the number of entries
!grep --invert-match "other biological processes" Blastquery-GOslim-BP.sorted.unique \
> Blastquery-GOslim-BP.sorted.unique.noOther
!head Blastquery-GOslim-BP.sorted.unique.noOther
!wc -l Blastquery-GOslim-BP.sorted.unique.noOther

XM_022430339.1	cell cycle and proliferation
XM_022430339.1	developmental processes
XM_022430339.1	other metabolic processes
XM_022430339.1	transport
XM_022430340.1	cell cycle and proliferation
XM_022430340.1	cell organization and biogenesis
XM_022430341.1	cell cycle and proliferation
XM_022430341.1	cell organization and biogenesis
XM_022430342.1	cell cycle and proliferation
XM_022430342.1	cell organization and biogenesis
  114704 Blastquery-GOslim-BP.sorted.unique.noOther


In [8]:
#Count the number of unique CGI IDs with defined GOSlim terms
!uniq -f1 Blastquery-GOslim-BP.sorted.unique.noOther | wc -l

  105959


## 4. Get Molecular Function GOslim terms

In [10]:
!awk -F"\t" '$3 == "F" { print $1"\t"$2 }' Blastquery-GOslim.tab | sort > Blastquery-GOslim-MF.sorted
!head Blastquery-GOslim-MF.sorted

XM_022430339.1	other molecular function
XM_022430339.1	other molecular function
XM_022430339.1	other molecular function
XM_022430339.1	other molecular function
XM_022430339.1	other molecular function
XM_022430340.1	other molecular function
XM_022430341.1	other molecular function
XM_022430342.1	other molecular function
XM_022430343.1	signal transduction activity
XM_022430343.1	signal transduction activity
